In [ ]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import json
import numpy as np
import scipy as sp
import scipy.stats as st
import scipy.integrate as integrate
from sklearn import linear_model

sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
sns_colors = sns.color_palette()
figsize = (15,8)
legend_fontsize = 16

from matplotlib import rc
rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('text.latex',preamble=r'\usepackage[utf8]{inputenc}')
rc('text.latex',preamble=r'\usepackage[russian]{babel}')
rc('figure', **{'dpi': 300})

## Выбор модели в полиномиальной регрессии

In [ ]:
## Оверфиттинг
## Исходная функция
orig = lambda x : np.sin(2*x)

## X-координаты точек данных
xd = np.arange(-1.5, 2, 7/60)
# xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
# xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
num_points = len(xd)

## Данные
data = orig(xd) + np.random.normal(0, .25, num_points)

## Для рисования
xs = np.arange(xd[0]-1.5, xd[-1]+1.5, 0.01)

## Обучаем модель с регуляризацией
def train_model(xs, ys, alpha=0, use_lasso=False):
    if alpha == 0:
        return linear_model.LinearRegression(fit_intercept=True).fit( xs, ys )
    else:
        if use_lasso:
            return linear_model.Lasso(alpha=alpha, fit_intercept=True).fit( xs, ys )
        else:
            return linear_model.Ridge(alpha=alpha, fit_intercept=True).fit( xs, ys )

In [ ]:
## Выделение полиномиальных признаков
xs_d = np.vstack([xs ** i for i in range(1, num_points+1)]).transpose()
xd_d = np.vstack([xd ** i for i in range(1, num_points+1)]).transpose()

## Какие степени многочлена будем обучать и рисовать
set_of_powers = [ 1, 3, 7 ]

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-2, 2))
ax.scatter(xd, data, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

for d in set_of_powers:
    if d == 0:
        print(np.mean(data))
        ax.hlines(np.mean(data), xmin=xs[0], xmax=xs[-1], label="$d=0$", linestyle="dashed")
    else:
        cur_model = train_model( xd_d[:, :d], data, alpha=0.1 )
        print(cur_model.coef_)
        ax.plot(xs, cur_model.predict( xs_d[:, :d] ), linewidth=2, label="$d=%d$" % d)

ax.legend(loc="lower center", fontsize=legend_fontsize)
# fig.savefig(output_directory + 'ms1.pdf', bbox_inches='tight')

In [ ]:
def get_X(d):
    return np.hstack([np.ones(xd_d[:, :d].shape[0]).reshape(-1, 1), xd_d[:, :d]])

In [ ]:
def linregr_sigma(X, y):
    N = X.shape[0]
    XtX = X.T.dot(X)
    mu = np.linalg.inv(XtX).dot(X.T).dot(data)
    preds = X.dot(mu)
    sigma2 = (np.sum((preds-data)**2) / N)
    return mu, sigma2

In [ ]:
N, dmax = data.shape[0], 12
lrs = [ linregr_sigma( get_X(d), data ) for d in range(1, dmax) ]

In [ ]:
def logL(lr, N, d):
    return -.5*N*(np.log(2*np.pi) + np.log(lr[1])+1)

def BIC(lr, N, d):
    return N*(np.log(2*np.pi) + np.log(lr[1]) + 1) + np.log(N)*(d+2)

def AIC(lr, N, d):
    return N*(np.log(2*np.pi) + np.log(lr[1]) + 1) + 2*(d+2)

In [ ]:
ds = np.arange(1, dmax)
logLs = [logL(lrs[d-1], N, d) for d in ds]
AICs = [AIC(lrs[d-1], N, d) for d in ds]
BICs = [BIC(lrs[d-1], N, d) for d in ds]

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((1, dmax-2))
ax.plot(ds, logLs, label='Логарифм правдоподобия', linewidth=2, marker='.', markersize=10)
ax.plot(ds, AICs, label="AIC", linewidth=2, marker='.', markersize=10)
ax.plot(ds, BICs, label="BIC", linewidth=2, marker='.', markersize=10)
ax.legend(fontsize=legend_fontsize)